In [2]:
import numpy as np
import csv
import plotly
import plotly.graph_objs as go
from PIL import Image, ImageDraw, ImageFont
from scipy.ndimage import gaussian_filter
from data import read_data

plotly.offline.init_notebook_mode(connected=True)
py = plotly.offline


In [339]:
from math import asin, acos, degrees, sin, cos, pi

def gamma(a, b, c):
    cosval = (a ** 2 + b ** 2 - c ** 2)/(2.0 * a * b)
    if cosval > 1.:
        cosval = 1.
    elif cosval < -1.:
        cosval = -1.
    return acos(cosval)

r = np.linalg.norm(np.array(pos_b8 - pos_17, dtype=np.float))
alpha = asin(v[1] / v[0])

def get_position_from_dist(r_17, r_b8):    
    beta = gamma(r_17, r, r_b8)
    return pos_17 + [r_17 * cos(alpha + beta), r_17 * sin(alpha + beta)]

def get_r_17_b8(point):
    r_17 = np.linalg.norm(point - pos_17)
    r_b8 = np.linalg.norm(point - pos_b8)
    return np.array([r_17, r_b8])

def reflect(point):
    return get_position_from_dist(*get_r_17_b8(point))
    
# now apply to our test data
# but we have them in order
# now we want to read them in a way so that we always have last reading from 17 and b8

with open('rssi_sat.csv', 'rb') as f:
    reader = csv.reader(f)
    rssi_17_b8 = []
    positions_17_b8 = []
    last_17 = -70
    last_b8 = -70
    for [b_id, rssi, x, y] in reader:
        rssi, x, y = int(rssi), (int(x) + 390.) / 3, (int(y) + 960.) / 3
        if b_id == '17' and rssi > -80:
            last_17 = rssi
            rssi_17_b8.append(np.array([last_17, last_b8], dtype=np.float))
            positions_17_b8.append(np.array([x, y], dtype=np.float))
        elif b_id == 'b8' and rssi > -80:
            last_b8 = rssi
            rssi_17_b8.append(np.array([last_17, last_b8], dtype=np.float))
            positions_17_b8.append(np.array([x, y], dtype=np.float))

rssi_17_b8 = np.array(rssi_17_b8, dtype=np.float)
positions_17_b8 = np.array(positions_17_b8, dtype=np.float)

dist_17 = dist_from_point(pos_17, points_17)
dist_b8 = dist_from_point(pos_b8, points_b8)

f_dist_rssi_17 = np.poly1d(np.polyfit(rssi_17, dist_17, 2))
f_dist_rssi_b8 = np.poly1d(np.polyfit(rssi_b8, dist_b8, 2))

def plot_f_dist_rssi(rssi, dist, f, title='', low=-100):
    domain = np.linspace(low, -50)
    py.iplot({
        "data": [
            go.Scatter(x=rssi, y=dist, mode='markers'),
            go.Scatter(x=domain, y=f(domain))
        ],
        "layout": go.Layout(title=title)
    })

# plot_f_dist_rssi(rssi_17, dist_17, f_dist_rssi_17)

In [336]:
# plot rssi as function of distance from beacon

def bestfit_rssi_dist(rssi, dist):
    return np.poly1d(np.polyfit(dist, rssi, 2))
    
def plot_rssi_f_dist(b_id, b_pos):
    (beacon_pos, beacon_rssi, dist) = beacon_fun(b_id, b_pos)
    f = bestfit_rssi_dist(beacon_rssi, dist)
    domain = np.linspace(0, 650)
    py.iplot({
        "data": [
            go.Scatter(x=dist, y=beacon_rssi, mode='markers'),
            go.Scatter(x=domain, y=f(domain))
        ],
        "layout": go.Layout(title=b_id)
    }) 

for (b_id, b_pos) in zip(beacon_ids, beacons_pixel):
    if len(data_for_beacon[b_id]) > 50:
        plot_rssi_f_dist(b_id, b_pos)

In [340]:
# okay now filter data from 17 and b8 for rssi > -80

rssi_17_80 = rssi_17[rssi_17 > -80]
rssi_b8_80 = rssi_b8[rssi_b8 > -80]

dist_17_80 = dist_17[rssi_17 > -80]
dist_b8_80 = dist_b8[rssi_b8 > -80]

f_dist_rssi_17_80 = np.poly1d(np.polyfit(rssi_17_80, dist_17_80, 3))
f_dist_rssi_b8_80 = np.poly1d(np.polyfit(rssi_b8_80, dist_b8_80, 3))

# plot_f_dist_rssi(rssi_17_80, dist_17_80, f_dist_rssi_17_80, low=-80, title='17')
# plot_f_dist_rssi(rssi_b8_80, dist_b8_80, f_dist_rssi_b8_80, low=-80, title='b8')

plot_f_dist_rssi(rssi_17, dist_17, f_dist_rssi_17, title='17')
plot_f_dist_rssi(rssi_b8, dist_b8, f_dist_rssi_b8, title='b8')

# def plot_f_rssi_dist(rssi, dist, f, title):
#     domain = np.linspace(0, 650)
#     py.iplot({
#         "data": [
#             go.Scatter(x=dist, y=rssi, mode='markers'),
#             go.Scatter(x=domain, y=f(domain))
#         ],
#         "layout": go.Layout(title=title)
#     }) 
    
# plot_f_rssi_dist(rssi_17_80, dist_17_80, np.poly1d(np.polyfit(dist_17_80, rssi_17_80, 3)), '17')
# plot_f_rssi_dist(rssi_b8_80, dist_b8_80, np.poly1d(np.polyfit(dist_b8_80, rssi_b8_80, 3)), 'b8')

In [331]:
from scipy.ndimage import gaussian_filter1d

def get_rel_dist_from_17_b8(rssi):
    return np.array([f_dist_rssi_17(rssi[0]), f_dist_rssi_b8(rssi[1])])

def get_pos_from_rssi(rssi):
    return get_position_from_dist(*get_rel_dist_from_17_b8(rssi))

def plot_predictions(rssi, positions, start, n):
    stop = start + n
    smooth_rssi = gaussian_filter1d(rssi, sigma=16, axis=0)
    estimated_position = np.apply_along_axis(get_pos_from_rssi, 1, smooth_rssi)
    
    py.iplot({
        "data": [
            go.Scatter(x=positions[start:stop,0], y=positions[start:stop,1]),
            go.Scatter(x=estimated_position[start:stop,0], y=estimated_position[start:stop,1])
        ],
        "layout": go.Layout(
            title='beacons',
            xaxis=dict(
                range=[-200, 800]
            ),
            yaxis=dict(
                range=[1050, 300]
            )
        )
    })
    
    py.iplot({
        "data": [
            go.Scatter(x=np.linspace(0, 100, n), y=positions[start:stop,0]),
            go.Scatter(x=np.linspace(0, 100, n), y=estimated_position[start:stop,0])
        ],
        "layout": go.Layout(
            title='x'
        )
    })
    
    py.iplot({
        "data": [
            go.Scatter(x=np.linspace(0, 100, n), y=positions[start:stop,1]),
            go.Scatter(x=np.linspace(0, 100, n), y=estimated_position[start:stop,1])
        ],
        "layout": go.Layout(
            title='y'
        )
    })


In [350]:
# let's restrict our selves to points with y < 600

close = positions_17_b8[:, 1] < 1000

plot_predictions(rssi_17_b8[close], positions_17_b8[close], 2500, 500)

correlation between 17 and b8

just triangulating on the two beacons is not enough; rssi varies too much
need to use kalman / bayesian

but also look at correlation between rssi from 17 and b8

could also look at max signal lately and use a rssi/dist which looks at the upper bound

if we use kalman / bayesian to model just the signal strength

we oscillate around the mean

but actually we want to be biased towards bigger values

need real data of walking in AT at walking speed

IDEA: now that I have my model, I can optimize the dist-f-rssi function 

as quad function which produces distances

two quad functions, therefore six parameters

error function on all of data

as we add deltas to our six parameters, look at the gradient and then adjust by that gradient

this is done by scipy minimize

In [320]:
# now for each beacon readings serially

def rssi_changes(b_id, b_pos, start, n):
    stop = start + n
    data = data_for_beacon[b_id]
    rssi = rssi_from_data(data)
    dist = dist_from_point(b_pos, pos_from_data(data))
    normalized_rssi = normalize(rssi)[start:stop]
    normalized_dist = normalize(dist)[start:stop]
    filtered_rssi = gaussian_filter(normalized_rssi, sigma=6)
    n = len(rssi)
    datalines = ['normalized_rssi', 'normalized_dist', 'filtered_rssi']

    py.iplot({
        'data': [go.Scatter(name=data, x=np.linspace(0, 100, n), y=locals()[data]) for data in datalines],
        'layout': go.Layout(title=b_id)
    })

for (b_id, b_pos) in zip(beacon_ids, beacons_pixel):
    if len(data_for_beacon[b_id]) > 20:
        rssi_changes(b_id, b_pos, 0, 6000)

In [304]:
# draw for all beacons

for b in beacon_ids:
    draw_image_for(b)

now plot rssi for b8 and 17 along different lines

one more plot: how x and y vary in time

one 





In [63]:
# more analytics

draw_image_for('17')

rssi = np.fromiter((row[1] for row in data), dtype=np.int16)
py.offline.iplot([go.Histogram(x=rssi)])

(beacon_b8_pos, beacon_b8_rssi, dist_b8) = beacon_fun('b8', np.array([161, 897]))
py.iplot({
    "data": [go.Scatter(x=dist_b8, y=beacon_b8_rssi, mode='markers')],
    "layout": go.Layout(title="hello world")
})

(beacon_17_pos, beacon_17_rssi, dist_17) = beacon_fun('17', np.array([356, 922]))

py.iplot({
    "data": [go.Scatter(x=dist_17, y=beacon_17_rssi, mode='markers')],
    "layout": go.Layout(title="hello world")
})

map_strongest_signal(beacon_b8_rssi, beacon_b8_pos, 50, 'b8')
map_strongest_signal(beacon_17_rssi, beacon_17_pos, 50, '17')

okay now look at all signals for a beacon and plot signal strength as function of distance

TODO cutoff at -90, take average (arithm/geom/harmonic) or median of rssi, and then plot on the map with different transparency

TODO triangulation with gaussians

In [ ]:
import math
import numpy as np
from numpy.random import randn

def compute_dog_data(z_var, process_var, count=1, dt=1.):
    "returns track, measurements 1D ndarrays"
    x, vel = 0., 1.
    z_std = math.sqrt(z_var) 
    p_std = math.sqrt(process_var)
    xs, zs = [], []
    for _ in range(count):
        v = vel + (randn() * p_std)
        x += v*dt        
        xs.append(x)
        zs.append(x + randn() * z_std)        
    return np.array(xs), np.array(zs)

In [ ]:
from filterpy.stats import plot_covariance_ellipse

dt = 0.3
F = np.array([[1, dt], [0, 1]])
x = np.array([10.0, 4.5])
P = np.diag([500, 500])
plot_covariance_ellipse(x, P, edgecolor='r')
x, P = predict(x, P, F, Q=0)
plot_covariance_ellipse(x, P, edgecolor='k', ls='dashed')

In [ ]:
from filterpy.common import Q_discrete_white_noise
Q = Q_discrete_white_noise(dim=2, dt=1., var=2.35)
print(Q)

In [ ]:
H = np.array([[1., 0.]])
R = np.array([[5.]])

In [ ]:
from filterpy.kalman import KalmanFilter
from filterpy.common import Q_discrete_white_noise

def pos_vel_filter(x, P, R, Q=0., dt=1.0):
    """ Returns a KalmanFilter which implements a
    constant velocity model for a state [x dx].T
    """
    
    kf = KalmanFilter(dim_x=2, dim_z=1)
    kf.x = np.array([x[0], x[1]]) # location and velocity
    kf.F = np.array([[1., dt],
                     [0.,  1.]])  # state transition matrix
    kf.H = np.array([[1., 0]])    # Measurement function
    kf.R *= R                     # measurement uncertainty
    if np.isscalar(P):
        kf.P *= P                 # covariance matrix 
    else:
        kf.P[:] = P               # [:] makes deep copy
    if np.isscalar(Q):
        kf.Q = Q_discrete_white_noise(dim=2, dt=dt, var=Q)
    else:
        kf.Q[:] = Q
    return kf

In [ ]:
dt = .1
x = np.array([0., 0.]) 
kf = pos_vel_filter(x, P=500, R=5, Q=0.1, dt=dt)

In [ ]:
# from kf_book.mkf_internal import plot_track

def run(x0=(0.,0.), P=500, R=0, Q=0, dt=1.0, 
        track=None, zs=None,
        count=0, do_plot=True, **kwargs):
    """
    track is the actual position of the dog, zs are the 
    corresponding measurements. 
    """

    # Simulate dog if no data provided. 
    if zs is None:
        track, zs = compute_dog_data(R, Q, count)

    # create the Kalman filter
    kf = pos_vel_filter(x0, R=R, P=P, Q=Q, dt=dt)  

    # run the kalman filter and store the results
    xs, cov = [], []
    for z in zs:
        kf.predict()
        kf.update(z)
        xs.append(kf.x)
        cov.append(kf.P)

    xs, cov = np.array(xs), np.array(cov)
#     if do_plot:
#         plot_track(xs[:, 0], track, zs, cov, 
#                    dt=dt, **kwargs)
    return xs, cov

In [ ]:
P = np.diag([500., 49.])
Ms, Ps = run(count=50, R=10, Q=0.01, P=P)